In [210]:
#IMPORTANT COMMMENTS ON LINES 2, 83-87, 91, 95
#pushift.io is a very popular API so requests may take long periods of time
import praw #pip install praw
import pandas as pd 
import datetime as dt
import requests
import numpy as np
# import xlsxwriter #pip install XlsxWriter
import json
import time
import math
import re
from multiprocessing import Pool
from functools import partial
from itertools import chain

import networkx as nx
import plotly.graph_objects as go
from networkx.algorithms import degree_centrality, betweenness_centrality, eigenvector_centrality

In [24]:
all_tickers = pd.read_csv('all_tickers.csv')
symbols = set(all_tickers['Symbol'].unique())

In [3]:
# reddit = praw.Reddit(
#     client_id="LtpWW1mpeoT7p4dRAVCeJA",
#     client_secret="YL-OwBXd1KkzvkpjbLDDERiYu7rskw",
#     password="utaustinmsba2022",
#     user_agent="SocialMediaAnalyticsProject",
#     username="vivekmehendiratta"
# )

In [556]:
# Custom function to create an edge between node x and node y, with a given text and width
def make_edge(x, y, text, width):
    return  go.Scatter(x         = x,
                       y         = y,
                       line      = dict(width = width,
                                   color = 'cornflowerblue'),
                       hoverinfo = 'text',
                       text      = ([text]),
                       mode      = 'lines')

def generateFigure(G):
    
#     edge_trace = []
    edge_x = []
    edge_y = []
    
    pos=nx.spring_layout(G)
        

    
    for edge in G.edges(data=True):
        x0, y0 = pos[edge[0]]
        x1, y1 = pos[edge[1]]
        
        edge_x.append(x0)
        edge_x.append(x1)
        edge_x.append(None)
        
        edge_y.append(y0)
        edge_y.append(y1)
        edge_y.append(None)
        
    edge_trace = go.Scatter(
        x=edge_x, y=edge_y,
        line={'color': 'cornflowerblue', 'width':1},
        hoverinfo='none',
        mode='lines')

    node_x = []
    node_y = []
    for node in G.nodes():
        x, y = pos[node]
        node_x.append(x)
        node_y.append(y)

    node_trace = go.Scatter(
        x=node_x, y=node_y,
        mode='markers',
        hoverinfo='text',
        marker=dict(
            showscale=True,
            # colorscale options
            #'Greys' | 'YlGnBu' | 'Greens' | 'YlOrRd' | 'Bluered' | 'RdBu' |
            #'Reds' | 'Blues' | 'Picnic' | 'Rainbow' | 'Portland' | 'Jet' |
            #'Hot' | 'Blackbody' | 'Earth' | 'Electric' | 'Viridis' |
            colorscale='YlGnBu',
            reversescale=True,
            color=[],
            size=10,
            colorbar=dict(
                thickness=15,
                title='Node Connections',
                xanchor='left',
                titleside='right'
            ),
            line_width=2))

    node_adjacencies = []
    node_text = []
    for node, adjacencies in zip(G.nodes(), G.adjacency()):
        node_adjacencies.append(len(adjacencies[1]))
        node_text.append(f'{node} # of connections: '+str(len(adjacencies[1])))

    node_trace.marker.color = node_adjacencies
    node_trace.text = node_text

    fig = go.Figure(data=[edge_trace, node_trace],
                 layout=go.Layout(
                    title='Network graph made with Python',
                    titlefont_size=16,
                    showlegend=False,
                    hovermode='closest',
                    margin=dict(b=20,l=5,r=5,t=40),
                    annotations=[ dict(
                        text = '',
                        showarrow=False,
                        xref="paper", yref="paper",
                        x=0.005, y=-0.002 ) ],
                    xaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
                    yaxis=dict(showgrid=False, zeroline=False, showticklabels=False))
                    )
    fig.show()

In [370]:
def makeCoMentions(x):
    if x['stock_mentions_x'] == x['stock_mentions_y']:
        return None
    
    a = min(x['stock_mentions_x'], x['stock_mentions_y'])
    b = max(x['stock_mentions_x'], x['stock_mentions_y'])
    tup = (a,b)
    return tup

In [25]:
# extract symbols from text 
def extract_symbols(content, symbols, strict=True):
    if pd.isna(content):
        return []
    
    if not strict:
        tokens = re.split(r'\W+', content.upper())
    else:
        tokens = content.split(' ')
    
    found = set()
    for token in tokens:
        if len(token) > 1:
            if token[0] == '$' or token[0] == ':':
                token = token[1:].upper()
            
            if token in symbols:
                found.add(token)
        
    return ','.join(found)

In [268]:
def getPushShiftData(**kwargs):
    url = f'https://api.pushshift.io/reddit/search/submission/'
    payload = kwargs
    request = requests.get(url, params=payload)
    return request.json()

def get_comment_info(submission_df):
    comment_list = []
    
    for submission_id in submission_df['id'].unique():
        submission = reddit.submission(id = submission_id)
        submission.comments.replace_more(limit=None)
        
        for comment in submission.comments.list():
            comment_dict = {}
            comment_dict['type'] = 'comment'
            comment_dict['depth'] = comment.depth + 1
            comment_dict['parent_id'] = comment.parent_id[3:]
            comment_dict['id'] = comment.id
            comment_dict['content'] = comment.body
            comment_dict['author_id'] = str(comment.author)
            comment_dict['date_epoch'] = comment.created_utc
            comment_dict['up_votes'] = comment.score
            comment_dict['ratio'] = 0.0
            comment_list.append(comment_dict)

            
    comment_df = pd.DataFrame(comment_list)

    return comment_df

In [21]:
# subreddit = 'walstreetbets'
# after = 1640995200 ## 2022-01-01
# time_diff = 86399 ## 24 hours
# before = after + time_diff
# sort_type = 'score'
# sort = 'desc'

# cols_to_keep = ['id', 'parent_id', 'body', 'author', 'score', 'parent_author', 'parent_body',
#                 'author_comment_karma', 'author_time_created', 'author_verified_email', 'author_is_mod', 
#                 'post_num_comments', 'post_flairs', 'post_title', 'post_url', 'post_upvote_ratio']

# cols_to_keep = ['type', 'depth', 'parent_id', 'id', 'content', 'author_id', 'date_epoch', 'up_votes', 'ratio']

# final_df = pd.DataFrame()
# while before <= 1643673600:
    
#     try:
#         print(after)
#         output = getPushShiftData(subreddit = subreddit, after = after, before=before, sort_type=sort_type, sort=sort)
#         submission_df = pd.json_normalize(output['data'])
#         submission_df['type'] = 'submission'
#         submission_df['depth'] = 0
#         submission_df['parent_id'] = ''
#         submission_df['content'] = submission_df['title'] + submission_df['selftext']
#         submission_df['author_id'] = submission_df['author']
#         submission_df['date_epoch'] = submission_df['created_utc']
#         submission_df['up_votes'] = submission_df['score']
#         submission_df['ratio'] = submission_df['upvote_ratio']
        
#         submission_df = submission_df[cols_to_keep]
#         final_df = final_df.append(submission_df, ignore_index=True)
        
#         comment_df = get_comment_info(submission_df)
#         final_df = final_df.append(comment_df, ignore_index=True)

#         final_df.to_csv(f'final_df_{before}.csv')
#     except Exception as e:
#         print(e)
#         pass
    
# #     break
    
#     after = before
#     before = after + time_diff

1640995200
1641081599
1641167998
1641254397
1641340796
1641427195
1641513594
1641599993
1641686392
1641772791
1641859190
1641945589
1642031988
1642118387
1642204786
1642291185
1642377584
1642463983
1642550382
1642636781
1642723180
1642809579
1642895978
1642982377
1643068776
1643155175
1643241574
1643327973
1643414372
1643500771
1643587170


In [22]:
# final_df['reach'] = final_df['up_votes'] * 1.0 / (final_df['depth'] + 0.001)

In [26]:
# final_df['stock_mentions'] = final_df['content'].apply(lambda x : extract_symbols(x, symbols))

In [27]:
# final_df.to_csv('Jan_Stocks.csv')

In [598]:
wsb = pd.read_csv('Jan_WSB.csv', index_col = 0)
stocks = pd.read_csv('Jan_Stocks.csv', index_col = 0)

In [599]:
wsb.shape, stocks.shape

((60537, 11), (24616, 11))

### Wall-street-bets subreddit analysis

In [600]:
wsb.head()

type  depth parent_id      id  \
0  submission      0       NaN  rtqa5y   
1  submission      0       NaN  rt8338   
2  submission      0       NaN  rtm2a5   
3  submission      0       NaN  rtma01   
4  submission      0       NaN  rtkkhd   

                                             content        author_id  \
0  Which one of you apes did this above the Rose ...  AvendiProkofiev   
1  New to investing (betting), but think I figure...         MCROCKS_   
2                                Theta gang[removed]        ECANNON08   
3                             Analysts in a nutshell         NewBlock   
4                            Down nearly 50% in 2021  NineteenEighty9   

     date_epoch  up_votes  ratio   reach stock_mentions  
0  1.641065e+09         2    1.0  2000.0            NaN  
1  1.641000e+09         2    1.0  2000.0         REE,RH  
2  1.641053e+09         1    1.0  1000.0            NaN  
3  1.641053e+09         1    1.0  1000.0            NaN  
4  1.641048e+09         1    1.0  1000.0            NaN

In [602]:
parent = wsb[['id', 'author_id']].drop_duplicates()

author_parent_child = parent.merge(wsb[['parent_id', 'author_id']], left_on='id', right_on='parent_id', suffixes=('_parent', '_child'))

author_parent_child = author_parent_child[
    (author_parent_child['author_id_parent']!= 'None') & 
    (author_parent_child['author_id_child']!='None')]

In [603]:
id_ncomments = author_parent_child['id'].value_counts().reset_index()
id_ncomments.columns = ['id', 'n_comments']

In [604]:
wsb_score = wsb.merge(id_ncomments, on='id', how='left')

wsb_score['n_comments'] = wsb_score['n_comments'].fillna(0)

wsb_score['score'] = 0.7*wsb_score['up_votes'] + 0.3*wsb_score['n_comments']

In [605]:
wsb_stock_mentions = wsb_score[~pd.isnull(wsb_score['stock_mentions'])]

In [606]:
wsb_id_mentions = wsb_stock_mentions[['id', 'stock_mentions']].set_index('id').apply(lambda x : x.str.split(',').explode()).reset_index()

In [607]:
wsb_stock_mentions = wsb_stock_mentions.merge(wsb_id_mentions, on='id', suffixes=('_combined', ''))
wsb_stock_mentions.drop('stock_mentions_combined', axis = 1, inplace = True)

In [608]:
co_mention_mapping = wsb_stock_mentions[['id', 'stock_mentions']].merge(wsb_stock_mentions[['id', 'stock_mentions', 'score']], 
                                                          left_on='id', 
                                                          right_on='id')

co_mention_mapping['co_mentions'] = co_mention_mapping.apply(lambda x : makeCoMentions(x), axis = 1)
co_mention_mapping.dropna(inplace = True)

co_mention_mapping.drop_duplicates(['id', 'co_mentions'], inplace=True)

M = nx.MultiGraph()
for i in co_mention_mapping.values:
    M.add_edge(i[1],i[2],weight=i[3])
    
# create weighted graph from M
G = nx.Graph()
for u,v,data in M.edges(data=True):
    w = data['weight'] if 'weight' in data else 1.0
    if G.has_edge(u,v):
        G[u][v]['weight'] += w
    else:
        G.add_edge(u, v, weight=w)

# G=nx.from_pandas_edgelist(co_mention_mapping, 'stock_mentions_x', 'stock_mentions_y', 'score')

generateFigure(G)

In [609]:
avg_mentions = int(np.mean(wsb_stock_mentions.groupby('stock_mentions').size()))

In [610]:
mentions_above_avg = set(wsb_stock_mentions.groupby('stock_mentions').size()[wsb_stock_mentions.groupby('stock_mentions').size() > avg_mentions].index)

In [611]:
wsb_stock_mentions = wsb_stock_mentions[wsb_stock_mentions['stock_mentions'].isin(mentions_above_avg)]

In [612]:
co_mention_mapping = wsb_stock_mentions[['id', 'stock_mentions']].merge(wsb_stock_mentions[['id', 'stock_mentions', 'score']], 
                                                          left_on='id', 
                                                          right_on='id')

co_mention_mapping['co_mentions'] = co_mention_mapping.apply(lambda x : makeCoMentions(x), axis = 1)
co_mention_mapping.dropna(inplace = True)

co_mention_mapping.drop_duplicates(['id', 'co_mentions'], inplace=True)

M = nx.MultiGraph()
for i in co_mention_mapping.values:
    M.add_edge(i[1],i[2],weight=i[3])
    
# create weighted graph from M
G = nx.Graph()
for u,v,data in M.edges(data=True):
    w = data['weight'] if 'weight' in data else 1.0
    if G.has_edge(u,v):
        G[u][v]['weight'] += w
    else:
        G.add_edge(u, v, weight=w)

# G=nx.from_pandas_edgelist(co_mention_mapping, 'stock_mentions_x', 'stock_mentions_y', 'score')

generateFigure(G)

In [613]:
id_count_above_1 = set(author_parent_child['author_id_parent'].value_counts()[(author_parent_child['author_id_parent'].value_counts() > 200)].index)
author_parent_child_filtered = author_parent_child[author_parent_child['author_id_parent'].isin(id_count_above_1)]

G=nx.from_pandas_edgelist(author_parent_child_filtered, 'author_id_parent', 'author_id_child', True)

generateFigure(G)

### Stocks subreddit analysis

In [594]:
parent = stocks[['id', 'author_id']].drop_duplicates()

author_parent_child = parent.merge(stocks[['parent_id', 'author_id']], left_on='id', right_on='parent_id', suffixes=('_parent', '_child'))

author_parent_child = author_parent_child[
    (~author_parent_child['author_id_parent'].isin(['AutoModerator', 'None'])) & 
    (author_parent_child['author_id_child']!='None')]

id_ncomments = author_parent_child['id'].value_counts().reset_index()
id_ncomments.columns = ['id', 'n_comments']

stocks_score = stocks.merge(id_ncomments, on='id', how='left')

stocks_score['n_comments'] = stocks_score['n_comments'].fillna(0)

stocks_score['score'] = 0.7*stocks_score['up_votes'] + 0.3*stocks_score['n_comments']

stocks_stock_mentions = stocks_score[~pd.isnull(stocks_score['stock_mentions'])]

stocks_id_mentions = stocks_stock_mentions[['id', 'stock_mentions']].set_index('id').apply(lambda x : x.str.split(',').explode()).reset_index()

stocks_stock_mentions = stocks_stock_mentions.merge(stocks_id_mentions, on='id', suffixes=('_combined', ''))
stocks_stock_mentions.drop('stock_mentions_combined', axis = 1, inplace = True)

co_mention_mapping = stocks_stock_mentions[['id', 'stock_mentions']].merge(stocks_stock_mentions[['id', 'stock_mentions', 'score']], 
                                                          left_on='id', 
                                                          right_on='id')

co_mention_mapping['co_mentions'] = co_mention_mapping.apply(lambda x : makeCoMentions(x), axis = 1)
co_mention_mapping.dropna(inplace = True)

co_mention_mapping.drop_duplicates(['id', 'co_mentions'], inplace=True)

M = nx.MultiGraph()
for i in co_mention_mapping.values:
    M.add_edge(i[1],i[2],weight=i[3])
    
# create weighted graph from M
G = nx.Graph()
for u,v,data in M.edges(data=True):
    w = data['weight'] if 'weight' in data else 1.0
    if G.has_edge(u,v):
        G[u][v]['weight'] += w
    else:
        G.add_edge(u, v, weight=w)

# G=nx.from_pandas_edgelist(co_mention_mapping, 'stock_mentions_x', 'stock_mentions_y', 'score')

generateFigure(G)




In [595]:
avg_mentions = int(np.mean(stocks_stock_mentions.groupby('stock_mentions').size()))

mentions_above_avg = set(stocks_stock_mentions.groupby('stock_mentions').size()[stocks_stock_mentions.groupby('stock_mentions').size() > avg_mentions].index)

stocks_stock_mentions = stocks_stock_mentions[stocks_stock_mentions['stock_mentions'].isin(mentions_above_avg)]

co_mention_mapping = stocks_stock_mentions[['id', 'stock_mentions']].merge(stocks_stock_mentions[['id', 'stock_mentions', 'score']], 
                                                          left_on='id', 
                                                          right_on='id')

co_mention_mapping['co_mentions'] = co_mention_mapping.apply(lambda x : makeCoMentions(x), axis = 1)
co_mention_mapping.dropna(inplace = True)

co_mention_mapping.drop_duplicates(['id', 'co_mentions'], inplace=True)

M = nx.MultiGraph()
for i in co_mention_mapping.values:
    M.add_edge(i[1],i[2],weight=i[3])
    
# create weighted graph from M
G = nx.Graph()
for u,v,data in M.edges(data=True):
    w = data['weight'] if 'weight' in data else 1.0
    if G.has_edge(u,v):
        G[u][v]['weight'] += w
    else:
        G.add_edge(u, v, weight=w)

# G=nx.from_pandas_edgelist(co_mention_mapping, 'stock_mentions_x', 'stock_mentions_y', 'score')

generateFigure(G)

In [596]:
id_count_above_1 = set(author_parent_child['author_id_parent'].value_counts()[(author_parent_child['author_id_parent'].value_counts() > 200)].index)
author_parent_child_filtered = author_parent_child[author_parent_child['author_id_parent'].isin(id_count_above_1)]

G=nx.from_pandas_edgelist(author_parent_child_filtered, 'author_id_parent', 'author_id_child', True)

generateFigure(G)